### 2018/2019 - Task List 10

1. Implement Naive Bayes classifier with pyro
    - create apropriate parameters (mean and std for a and b, sigma - noise)
    - provide optimization procedure
    - check appropriateness of implemented method with selected dataset


# Required imports

In [69]:
%matplotlib inline
import pyro
import torch
import numpy as np
import matplotlib.pyplot as plt
import pyro.optim as optim
import pyro.distributions as dist
from torch.distributions import constraints
from tqdm import tqdm
import seaborn as sns
from matplotlib import animation, rc
from IPython.display import HTML
import torch.nn as nn
from functools import partial
import pandas as pd
from pyro.contrib.autoguide import AutoDiagonalNormal
from pyro.infer import EmpiricalMarginal, SVI, Trace_ELBO, TracePredictive
from sklearn.base import BaseEstimator
import scipy.stats

In [2]:
pyro.set_rng_seed(1)
pyro.enable_validation(True)

In [3]:
from sklearn import datasets, model_selection
from sklearn.naive_bayes import GaussianNB


## Solutions

### sklearn solution

In [4]:
torch.set_default_tensor_type(torch.DoubleTensor)

In [5]:
iris = datasets.load_iris()

gnb = GaussianNB()


X_train, X_validation, Y_train, Y_validation = model_selection.train_test_split(
    iris.data, iris.target, test_size=0.33, random_state=5)

In [7]:
kfold = 5
scoring = ['accuracy', 'f1_micro', 'f1_macro']
cv_results = model_selection.cross_validate(gnb, X_train, Y_train, cv=kfold, scoring=scoring)

#displaying the mean and standard deviation of the prediction
for score in scoring: 
    msg = "%s: %f (%f)" % ('NB ' + score, cv_results['test_' + score].mean(), cv_results['test_' + score].std())
    print(msg)

NB accuracy: 0.960902 (0.035958)
NB f1_micro: 0.960902 (0.035958)
NB f1_macro: 0.960191 (0.036241)


### self-made NB

In [73]:
class NaiveBayesClassifier(BaseEstimator):
    
    def __init__(self):
        pass
    
    def fit(self, x_data, y_data):
        self.x = x_data
        self.y = y_data
        self.attributes_number = x_data.shape[1]
        self.classes = np.unique(y_data)
        
        div_data = self.div_by_category_and_attribute(self.x, self.y)
        self.params = {}
        for key in div_data.keys():
            mean, scale, losses = self.train(div_data[key], key)
            self.params[key] = {"mean":mean, "scale":scale}
        
    
    def predict(self, data):
        predictions = list()

        for x in data:
            max_prob = -1
            prediction = None
            for category in self.classes:
                for attr in range(self.attributes_number):
                    mean = self.params[(category, attr)]['mean'].item()
                    scale = self.params[(category, attr)]['scale'].item()
                    prob = scipy.stats.norm(mean, scale).pdf(x[attr])
                    print(prob)
                    if max_prob < prob:
                        max_prob = prob
                        prediction = category
            predictions.append(prediction)
        return predictions
    
    def div_by_category_and_attribute(self, x_data, y_data):
        X_cl = {}

        for i in range(len(x_data)):
            for attribute in range(len(x_data[0])):
                if (y_data[i], attribute) not in X_cl.keys():
                    X_cl[(y_data[i], attribute)] = list()
                X_cl[(y_data[i], attribute)].append(x_data[i][attribute])

        for cl_key in np.unique(y_data):
            for attribute in range(len(x_data[0])):
                X_cl[cl_key, attribute] = np.array(X_cl[cl_key, attribute])

        return X_cl
    
    def model(self, x_data, label):
        mean = pyro.param('mean' + str(label),  torch.tensor(np.random.choice(x_data, 1)).double())
        scale = pyro.param('scale' + str(label), torch.tensor(1.0).double(), constraint=constraints.positive)
        with pyro.plate('data_loop' + str(label), len(x_data)):
            pyro.sample('prob' + str(label), dist.Normal(mean, scale), obs=x_data)

    def guide(self, x_data, label):
        mean = pyro.param('mean' + str(label), torch.tensor(2.0))
        scale = pyro.param('scale' + str(label), torch.tensor(1.0), constraint=constraints.positive)
        pyro.sample('prob' + str(label), dist.Normal(mean.double(), scale.double()), infer={'is_auxiliary': True})
        
    def train(self, data, label, num_steps=1000):
        pyro.clear_param_store()

        optim = pyro.optim.Adam({"lr": 0.045})
        svi = pyro.infer.SVI(model=self.model,
                             guide=self.guide,
                             optim=optim,
                             loss=pyro.infer.Trace_ELBO(),
                             num_samples=len(data))

        losses = []
        print("Learning for class: " + str(label[0]) + " and attribute: " + str(label[1]))
        t = tqdm(range(num_steps))
        for j in t:
            loss = svi.step(torch.from_numpy(data), label)
            losses.append(loss)
            t.set_postfix(loss=loss)
        return pyro.param("mean" + str(label)), pyro.param("scale" + str(label)), losses

    

In [75]:
nbc = NaiveBayesClassifier()

In [76]:
kfold = 5
scoring = ['accuracy', 'f1_micro', 'f1_macro']
cv_results = model_selection.cross_validate(nbc, X_train, Y_train, cv=kfold, scoring=scoring)

#displaying the mean and standard deviation of the prediction
for score in scoring: 
    msg = "%s: %f (%f)" % ('NB ' + score, cv_results['test_' + score].mean(), cv_results['test_' + score].std())
    print(msg)





  0%|          | 0/1000 [00:00<?, ?it/s]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=326]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=296]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=269]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=244]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=223]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=206]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=190]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=175]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=163]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=152]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=142]



  0%|          | 0/1000 [00:00<?, ?it/s, loss=131]



  1%|          | 12/1000 [00:00<00:08, 113.17it/s, loss=131]



  1%|          | 12/1000 [00:00<00:08, 113.17it/s, loss=127]



  1%|          | 12/1000 [00:00<00:08, 113.17it/s, loss=120]



  1%|          | 12/1000 [00:00<00:08, 113.17it/s, loss=114]



  1%|          | 12/1000 [00:00<00:08, 113.17it/

Learning for class: 2 and attribute: 0






  1%|          | 12/1000 [00:00<00:08, 113.17it/s, loss=88.7]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=88.7]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=87.8]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=86]  



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=83.2]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=83]  



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=81.7]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=80.6]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=76.5]



  2%|▏         | 22/1000 [00:00<00:09, 108.13it/s, loss=78.7]



  3%|▎         | 30/1000 [00:00<00:10, 94.91it/s, loss=78.7] 



  3%|▎         | 30/1000 [00:00<00:10, 94.91it/s, loss=77]  



  3%|▎         | 30/1000 [00:00<00:10, 94.91it/s, loss=77.1]



  3%|▎         | 30/1000 [00:00<00:10, 94.91it/s, loss=76.5]



  3%|▎         | 30/1000 [00:00<00:10, 94.91it/s, loss=75.5]



  3%|▎         | 30/1000 

 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=64.6]



 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=63.2]



 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=64.6]



 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=64.4]



 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=64.3]



 12%|█▏        | 116/1000 [00:00<00:06, 132.43it/s, loss=64.1]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=64.2]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=63.4]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=63.8]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=63.9]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=63.8]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=61.1]



 12%|█▏        | 116/1000 [00:01<00:06, 132.43it/s, loss=63.6]



 13%|█▎        | 132/1000 [00:01<00:06, 139.18it/s, loss=63.6]



 13%|█▎        | 132/1000 [00:01<00:06, 139.18it/s, loss=63.2]



 13%|█▎   

 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=48.2]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=47.9]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=47.7]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=44.5]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=47.2]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=46]  



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=46.5]



 21%|██        | 212/1000 [00:01<00:05, 136.51it/s, loss=46.1]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=46.1]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=46.1]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=44.2]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=45.6]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=43.7]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=45.1]



 23%|██▎       | 226/1000 [00:01<00:06, 128.07it/s, loss=44.8]



 23%|██▎  

...

0.0202341137722982
0.0003593477547332832
0.843065565330727
0.9928687194144848
1.3778969014533402
4.228417997311414
0.07969194680293044
0.18497967504217236
8.350913757386978e-07
7.367197598668124e-07
0.002980716500261442
0.5652272584127779
6.255480864779489e-13
5.9460788571104245e-12
0.05545933887944675
0.003825828020756472
4.390900813751911e-42
3.803117001485639e-16
0.7391012882585558
0.35013554559995846
0.6923363067916963
0.5872375435770835
0.4020706533649716
0.05998541639374014
0.01188951453782453
0.0003593477547332832
0.00329221757089096
0.6044233843662931
8.433463939612936e-105
9.405973322258745e-67
0.5086359581038832
0.6627479492794597
0.038828091600547454
0.12402706828468935
0.6907450454722724
1.1703414312828715
0.7604618888730641
1.0147445467363543
0.00021108238438758523
0.03751958844619528
9.716613751273891e-121
9.405973322258745e-67
0.26646085848496226
0.911810287213716
0.0076201303779522105
0.12402706828468935
0.723980736711118
0.3812623055828646
0.654555013203576
1.014744546

0.7568340395452013
1.7917039431894317
0.7375084685038862
1.2324435147255528
0.08018773502895198
0.06641117144641119
0.9342451410685266
0.9928687194144848
2.127344963430465
1.5917821585635663
0.11623430018554726
0.05224338868356828
9.738528989830951e-08
4.6470945705582136e-08
0.005413224969895313
0.21588625119599814
3.38190071941274e-14
3.141129877593538e-13
0.00021108238438758523
0.4487566695588163
9.445141503112158e-81
1.546264880401351e-58
0.26646085848496226
0.8595001395877189
0.26872272272615405
0.344824311629007
0.723980736711118
1.2324435147255528
0.47189078634832826
0.6483694977126371
0.00021108238438758523
0.4487566695588163
5.404678563479738e-90
6.220703013436451e-116
0.26646085848496226
0.8595001395877189
0.13931991856262976
2.146198611178176e-05
0.723980736711118
1.2324435147255528
0.6369481767830152
0.9206191889515253
0.3582604593923819
0.3118462300716383
3.8775972631234634e-30
4.494645784224651e-31
0.614663590734237
1.0261753069731012
0.3395069813626293
1.933290413373144
0

0.843065565330727
0.9928687194144848
1.3778969014533402
4.228417997311414
0.07969194680293044
0.18497967504217236
8.350913757386978e-07
7.367197598668124e-07
0.002980716500261442
0.5652272584127779
6.255480864779489e-13
5.9460788571104245e-12
0.05545933887944675
0.003825828020756472
4.390900813751911e-42
3.803117001485639e-16
0.7391012882585558
0.35013554559995846
0.6923363067916963
0.5872375435770835
0.4020706533649716
0.05998541639374014
0.01188951453782453
0.0003593477547332832
0.00329221757089096
0.6044233843662931
8.433463939612936e-105
9.405973322258745e-67
0.5086359581038832
0.6627479492794597
0.038828091600547454
0.12402706828468935
0.6907450454722724
1.1703414312828715
0.7604618888730641
1.0147445467363543
0.00021108238438758523
0.03751958844619528
9.716613751273891e-121
9.405973322258745e-67
0.26646085848496226
0.911810287213716
0.0076201303779522105
0.12402706828468935
0.723980736711118
0.3812623055828646
0.654555013203576
1.0147445467363543
0.0072968367161316515
0.899045588

8.297045103230127e-10
7.367197598668124e-07
0.0008156815291719259
0.21588625119599814
6.389815055642707e-17
5.9460788571104245e-12
0.0005599473712354343
0.4487566695588163
4.837100722865832e-56
3.9523821506106965e-37
0.34227276688879194
0.8595001395877189
0.7568340395452013
1.7917039431894317
0.7375084685038862
1.2324435147255528
0.08018773502895198
0.06641117144641119
0.9342451410685266
0.9928687194144848
2.127344963430465
1.5917821585635663
0.11623430018554726
0.05224338868356828
9.738528989830951e-08
4.6470945705582136e-08
0.005413224969895313
0.21588625119599814
3.38190071941274e-14
3.141129877593538e-13
0.00021108238438758523
0.4487566695588163
9.445141503112158e-81
1.546264880401351e-58
0.26646085848496226
0.8595001395877189
0.26872272272615405
0.344824311629007
0.723980736711118
1.2324435147255528
0.47189078634832826
0.6483694977126371
0.00021108238438758523
0.4487566695588163
5.404678563479738e-90
6.220703013436451e-116
0.26646085848496226
0.8595001395877189
0.13931991856262976

0.44350585581007806
0.12402706828468935
0.4020706533649716
1.2324435147255528
0.3022882540041494
1.0147445467363543
0.15889840193314556
0.12347511351325911
2.196254674119184e-45
3.803117001485639e-16
0.7227134634348645
1.1413186787979135
0.7505403993361383
0.5872375435770835
0.2498827091316347
0.8117161864221712
0.0202341137722982
0.0003593477547332832
0.843065565330727
0.9928687194144848
1.3778969014533402
4.228417997311414
0.07969194680293044
0.18497967504217236
8.350913757386978e-07
7.367197598668124e-07
0.002980716500261442
0.5652272584127779
6.255480864779489e-13
5.9460788571104245e-12
0.05545933887944675
0.003825828020756472
4.390900813751911e-42
3.803117001485639e-16
0.7391012882585558
0.35013554559995846
0.6923363067916963
0.5872375435770835
0.4020706533649716
0.05998541639374014
0.01188951453782453
0.0003593477547332832
0.00329221757089096
0.6044233843662931
8.433463939612936e-105
9.405973322258745e-67
0.5086359581038832
0.6627479492794597
0.038828091600547454
0.12402706828468